## Portfolio Optimizer

In [102]:
# Portfolio consists of 10 stocks
import random
import numpy as np
import datetime as dt
import pandas as pd
import yfinance as yf
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
import cufflinks as cf
cf.go_offline()
# Define the list of stock tickers
tickers = ['AMZN', 'JPM', 'META', 'PG', 'GOOG', 'CAT', 'PFE', 'EXC', 'DE', 'JNJ']
# Download historical data for these stocks
data = yf.download(tickers, start='2014-01-01', end='2023-01-01')
close_price_df = data['Close']
close_price_df.head()

[*********************100%***********************]  10 of 10 completed


Ticker                          AMZN        CAT         DE        EXC  \
Date                                                                    
2014-01-02 00:00:00+00:00  19.898500  89.870003  90.260002  19.379457   
2014-01-03 00:00:00+00:00  19.822001  89.820000  90.660004  18.987162   
2014-01-06 00:00:00+00:00  19.681499  88.639999  89.910004  19.108418   
2014-01-07 00:00:00+00:00  19.901501  88.930000  90.309998  19.208275   
2014-01-08 00:00:00+00:00  20.096001  89.139999  89.339996  19.165478   

Ticker                          GOOG        JNJ        JPM       META  \
Date                                                                    
2014-01-02 00:00:00+00:00  27.724083  91.029999  58.209999  54.709999   
2014-01-03 00:00:00+00:00  27.521841  91.849998  58.660000  54.560001   
2014-01-06 00:00:00+00:00  27.828691  92.330002  59.000000  57.200001   
2014-01-07 00:00:00+00:00  28.365179  94.290001  58.320000  57.919998   
2014-01-08 00:00:00+00:00  28.424210  94.160004  58.869999  58.230000   

Ticker                           PFE         PG  
Date                                             
2014-01-02 00:00:00+00:00  28.899431  80.540001  
2014-01-03 00:00:00+00:00  28.956356  80.449997  
2014-01-06 00:00:00+00:00  28.984819  80.639999  
2014-01-07 00:00:00+00:00  29.165085  81.419998  
2014-01-08 00:00:00+00:00  29.364326  80.239998

#### Scaling Prices, assigning weights to portfolio

In [103]:
# Number of stocks under consideration
n = len(close_price_df.columns) 

# Function scales stock prices based on their initial starting price
def price_scaling(raw_prices_df):
    scaled_prices_df = raw_prices_df.copy()
    # Loop through each column in the df
    for i in raw_prices_df.columns:
        # Divide each price by the first price in the column
        scaled_prices_df[i] = raw_prices_df[i] / raw_prices_df[i].iloc[0] # Normalize the prices
    return scaled_prices_df

# Function generates random weights for the portfolio
def generate_portfolio_weights(n):
    weights = []
    for i in range(n):
        weights.append(random.random())
    # Ensures the sum of all weights add up to 1
    weights = weights/np.sum(weights)
    return weights

scaled_df = price_scaling(close_price_df) # Create df of scaled prices
weights = generate_portfolio_weights(n)

print('Number of stocks under consideration = {}'.format(n))
print('Random Portfolio weights = {}'.format(np.round(weights, 2)))
scaled_df.head()

Number of stocks under consideration = 10
Random Portfolio weights = [0.16 0.   0.08 0.1  0.04 0.16 0.06 0.17 0.09 0.13]


Ticker                         AMZN       CAT        DE       EXC      GOOG  \
Date                                                                          
2014-01-02 00:00:00+00:00  1.000000  1.000000  1.000000  1.000000  1.000000   
2014-01-03 00:00:00+00:00  0.996155  0.999444  1.004432  0.979757  0.992705   
2014-01-06 00:00:00+00:00  0.989095  0.986314  0.996122  0.986014  1.003773   
2014-01-07 00:00:00+00:00  1.000151  0.989540  1.000554  0.991167  1.023124   
2014-01-08 00:00:00+00:00  1.009925  0.991877  0.989807  0.988958  1.025253   

Ticker                          JNJ       JPM      META       PFE        PG  
Date                                                                         
2014-01-02 00:00:00+00:00  1.000000  1.000000  1.000000  1.000000  1.000000  
2014-01-03 00:00:00+00:00  1.009008  1.007731  0.997258  1.001970  0.998882  
2014-01-06 00:00:00+00:00  1.014281  1.013572  1.045513  1.002955  1.001242  
2014-01-07 00:00:00+00:00  1.035812  1.001890  1.058673  1.009192  1.010926  
2014-01-08 00:00:00+00:00  1.034384  1.011338  1.064339  1.016087  0.996275

#### Getting Portfolio Returns
Value of Portfolio = $ invested * (weights and stock values)

In [104]:
# Function returns a DataFrame with: stock values, portfolio values, and percentage daily return of the portfolio
def asset_allocation(df, weights, initial_investment):
    portfolio_df = df.copy()  # Create a copy of the DataFrame
    # Scale stock prices using the "price_scaling" function that we defined earlier (Make them all start at 1)
    scaled_df = price_scaling(df)
    # Assigns a weight to each stock in the portfolio
    for i, stock in enumerate(scaled_df.columns):
        portfolio_df[stock] = scaled_df[stock] * weights[i] * initial_investment
    
    # Sum up all values and place the result in a new column titled "Value"
    portfolio_df['Portfolio Value'] = portfolio_df.loc[:, portfolio_df.columns != 'Date'].sum(axis=1, numeric_only=True)
    # Calculate the portfolio percentage daily return and replace NaNs with zeros
    portfolio_df['% Daily Returns'] = portfolio_df['Portfolio Value'].pct_change().fillna(0)
    return portfolio_df

initial_investment = 10000
# Call the function
portfolio_df = asset_allocation(close_price_df, weights, initial_investment)
portfolio_df.head()

Ticker                            AMZN       CAT          DE          EXC  \
Date                                                                        
2014-01-02 00:00:00+00:00  1577.232480  7.079625  811.538834  1029.446627   
2014-01-03 00:00:00+00:00  1571.168797  7.075686  815.135297  1008.607672   
2014-01-06 00:00:00+00:00  1560.032140  6.982730  808.391954  1015.048846   
2014-01-07 00:00:00+00:00  1577.470292  7.005575  811.988349  1020.353318   
2014-01-08 00:00:00+00:00  1592.887115  7.022118  803.266948  1018.079915   

Ticker                           GOOG          JNJ         JPM         META  \
Date                                                                          
2014-01-02 00:00:00+00:00  396.879835  1587.727412  604.438934  1724.043542   
2014-01-03 00:00:00+00:00  393.984673  1602.029686  609.111636  1719.316753   
2014-01-06 00:00:00+00:00  398.377343  1610.401811  612.642118  1802.509478   
2014-01-07 00:00:00+00:00  406.057348  1644.587731  605.581155  1825.198327   
2014-01-08 00:00:00+00:00  406.902390  1642.320344  611.292217  1834.967215   

Ticker                            PFE           PG  Portfolio Value  \
Date                                                                  
2014-01-02 00:00:00+00:00  934.327263  1327.285449     10000.000000   
2014-01-03 00:00:00+00:00  936.167659  1325.802199      9988.400059   
2014-01-06 00:00:00+00:00  937.087888  1328.933407     10080.407715   
2014-01-07 00:00:00+00:00  942.915923  1341.787653     10182.945671   
2014-01-08 00:00:00+00:00  949.357465  1322.341450     10188.437179   

Ticker                     % Daily Returns  
Date                                        
2014-01-02 00:00:00+00:00         0.000000  
2014-01-03 00:00:00+00:00        -0.001160  
2014-01-06 00:00:00+00:00         0.009211  
2014-01-07 00:00:00+00:00         0.010172  
2014-01-08 00:00:00+00:00         0.000539

#### Plotting Portfolio

In [105]:
# Define a function that performs interactive data visualization using Plotly Express
def plot_financial_data(df, title):
    fig = px.line(title = title)
    # For loop that plots all stock prices in the pandas dataframe df
    for i in df.columns[0:]:
        fig.add_scatter(x = df.index, y = df[i], name = i)
        fig.update_traces(line_width = 3)
        fig.update_layout({'plot_bgcolor': "white"})
    fig.show()

# Plot each stock position in our portfolio over time
plot_financial_data(portfolio_df.drop(['Portfolio Value', '% Daily Returns'], axis = 1), 'Portfolio positions [$]')
# Plot the total daily value of the portfolio (sum of all positions)
plot_financial_data(portfolio_df[['Portfolio Value']], 'Total Portfolio Value [$]')
# Plot the portfolio percentage daily return
plot_financial_data(portfolio_df[['% Daily Returns']], 'Portfolio Percentage Daily Return [%]')

$$ \text{Sharpe Ratio} = \frac{\text{Portfolio Return} - \text{Risk-Free Rate}}{\text{Portfolio Standard Deviation}} $$

In [106]:
# Simulation engine function: performs asset allocation, calculates portfolio statistical metrics including Sharpe ratio
# The function receives: portfolio weights and initial investment amount
# The function returns: Expected return, Expected volatility, Sharpe ratio, Return on investment, Final value in dollars
def simulation_engine(weights, initial_investment):
    # Perform asset allocation using the random weights (sent as arguments to the function)
    portfolio_df = asset_allocation(close_price_df, weights, initial_investment)
    # Return on investment is calculated using the last final value of the portfolio compared to its initial value
    return_on_investment = ((portfolio_df['Portfolio Value'].iloc[-1:] - portfolio_df['Portfolio Value'].iloc[0])
                            / portfolio_df['Portfolio Value'].iloc[0]) * 100
    # Daily change of every stock in the portfolio (Note that we dropped the portfolio daily worth and daily % returns) 
    portfolio_daily_return_df = portfolio_df.drop(columns = ['Portfolio Value', '% Daily Returns'])
    portfolio_daily_return_df = portfolio_daily_return_df.pct_change(1) 
    # Portfolio Expected Return formula
    expected_portfolio_return = np.sum(weights * portfolio_daily_return_df.mean() ) * 252
    # Portfolio volatility (risk) formula
    # Risk of asset measured using standard deviation (cannot sum the risks of the individual assets)
    # Portfolio risk must consider correlations between assets within the portfolio which is indicated by the covariance 
    # The covariance determines the relationship between the movements of two random variables (moving together or inversely)
    covariance = portfolio_daily_return_df.cov() * 252 
    expected_volatility = np.sqrt(np.dot(weights.T, np.dot(covariance, weights)))
    # Risk-free rate of return (rf) is the minimum return an investor expects for any investment
    rf = 0.03
    # Calculate Sharpe ratio
    sharpe_ratio = (expected_portfolio_return - rf)/expected_volatility 
    return expected_portfolio_return, expected_volatility, sharpe_ratio, portfolio_df['Portfolio Value'].iloc[-1:].values[0], return_on_investment.values[0]

# Let's test out the "simulation_engine" function and print out statistical metrics
portfolio_metrics = simulation_engine(weights, initial_investment)
print('Expected Portfolio Annual Return = {:.2f}%'.format(portfolio_metrics[0] * 100))
print('Portfolio Standard Deviation (Volatility) = {:.2f}%'.format(portfolio_metrics[1] * 100))
print('Sharpe Ratio = {:.2f}'.format(portfolio_metrics[2]))
print('Portfolio Final Value = ${:.2f}'.format(portfolio_metrics[3]))
print('Return on Investment = {:.2f}%'.format(portfolio_metrics[4]))

Expected Portfolio Annual Return = 14.01%
Portfolio Standard Deviation (Volatility) = 18.08%
Sharpe Ratio = 0.61
Portfolio Final Value = $26518.72
Return on Investment = 165.19%


### Monte Carlo Simulation

In [114]:
# Set the number of simulation runs
sim_runs = 1000
initial_investment = 10000

# Placeholder to store values
weights_runs = np.zeros((sim_runs, n))
sharpe_ratio_runs = np.zeros(sim_runs)
expected_portfolio_returns_runs = np.zeros(sim_runs)
volatility_runs = np.zeros(sim_runs)
return_on_investment_runs = np.zeros(sim_runs)
final_value_runs = np.zeros(sim_runs)

for i in range(sim_runs):
    # Generate random weights 
    weights = generate_portfolio_weights(n)
    # Store the weights
    weights_runs[i,:] = weights
    # Call "simulation_engine" function and store Sharpe ratio, return and volatility
    # Note that asset allocation is performed using the "asset_allocation" function  
    expected_portfolio_returns_runs[i], volatility_runs[i], sharpe_ratio_runs[i], final_value_runs[i], return_on_investment_runs[i] = simulation_engine(weights, initial_investment)
    #print("Simulation Run = {}, Final Value = ${:.2f}, Sharpe Ratio = {:.2f}".format((i+1),final_value_runs[i], sharpe_ratio_runs[i]))   


In [120]:
# List all Sharpe ratios generated from the simulation
sharpe_ratio_runs
# Return the index of the maximum Sharpe ratio (Best simulation run) 
sharpe_ratio_runs.argmax()
# Return the maximum Sharpe ratio value
sharpe_ratio_runs.max()
weights_runs
# Obtain the portfolio weights that correspond to the maximum Sharpe ratio (Golden set of weights!)
weights_runs[sharpe_ratio_runs.argmax(), :]
# Return Sharpe ratio, volatility corresponding to the best weights allocation (maximum Sharpe ratio)
optimal_portfolio_return, optimal_volatility, optimal_sharpe_ratio, highest_final_value, optimal_return_on_investment = simulation_engine(weights_runs[sharpe_ratio_runs.argmax(), :], initial_investment)
# Create DataFrame with volatility, return, and Sharpe ratio for all simualation runs
sim_out_df = pd.DataFrame({'Volatility': volatility_runs.tolist(), 'Portfolio_Return': expected_portfolio_returns_runs.tolist(), 'Sharpe_Ratio': sharpe_ratio_runs.tolist() })

print('Best Portfolio Metrics Based on {} Monte Carlo Simulation Runs:'.format(sim_runs))
print('  - Portfolio Expected Annual Return = {:.02f}%'.format(optimal_portfolio_return * 100))
print('  - Portfolio Standard Deviation (Volatility) = {:.02f}%'.format(optimal_volatility * 100))
print('  - Sharpe Ratio = {:.02f}'.format(optimal_sharpe_ratio))
print('  - Final Value = ${:.02f}'.format(highest_final_value))
print('  - Return on Investment = {:.02f}%'.format(optimal_return_on_investment))

Best Portfolio Metrics Based on 1000 Monte Carlo Simulation Runs:
  - Portfolio Expected Annual Return = 17.02%
  - Portfolio Standard Deviation (Volatility) = 20.26%
  - Sharpe Ratio = 0.69
  - Final Value = $33561.82
  - Return on Investment = 235.62%


In [138]:
# Create a figure for Portfolio Return and Volatility
fig = px.line(sim_out_df, x=sim_out_df.index, y='Portfolio_Return', title='Portfolio Return and Volatility Over Time')
fig.update_traces(line_color='red', name='Portfolio Return')
# Add Volatility to the same figure
fig.add_scatter(x=sim_out_df.index, y=sim_out_df['Volatility'], mode='lines', name='Volatility', line=dict(color='blue'))
# Update layout
fig.update_layout(
    xaxis_title="Date",
    yaxis_title="Value",
)
# Show plot
fig.show()
# Plot interactive plot for Sharpe Ratio
fig3 = px.line(sim_out_df, x=sim_out_df.index, y='Sharpe_Ratio', title='Sharpe Ratio Over Time')
fig3.update_traces(line_color='purple')
fig3.update_layout(
    xaxis_title="Date",
    yaxis_title="Sharpe Ratio",
)
fig3.show()

In [135]:
# Plot volatility vs. return for all simulation runs
# Highlight the volatility and return that corresponds to the highest Sharpe ratio
fig = px.scatter(sim_out_df, x = 'Volatility', y = 'Portfolio_Return', color = 'Sharpe_Ratio', size = 'Sharpe_Ratio', hover_data = ['Sharpe_Ratio'] )
fig.update_layout({'plot_bgcolor': "white"})
fig.show()
# Use this code if Sharpe ratio is negative
# fig = px.scatter(sim_out_df, x = 'Volatility', y = 'Portfolio_Return', color = 'Sharpe_Ratio', hover_data = ['Sharpe_Ratio'] )


In [136]:
# Let's highlight the point with the highest Sharpe ratio
fig = px.scatter(sim_out_df, x = 'Volatility', y = 'Portfolio_Return', color = 'Sharpe_Ratio', size = 'Sharpe_Ratio', hover_data = ['Sharpe_Ratio'] )
fig.add_trace(go.Scatter(x = [optimal_volatility], y = [optimal_portfolio_return], mode = 'markers', name = 'Optimal Point', marker = dict(size=[40], color = 'red')))
fig.update_layout(coloraxis_colorbar = dict(y = 0.7, dtick = 5))
fig.update_layout({'plot_bgcolor': "white"})
fig.show()